In [1]:
from tensorflow import keras
import os
import joblib
import numpy as np
from explain import  get_relevance, get_critical_neurons
import tensorflow as tf
# from tensorflow import set_random_seed
from scalelayer import  ScaleLayer
from numpy.random import seed
import itertools
import time
import copy
from preprocessing import pre_census_income
import tensorflow.keras.backend as K
import argparse
from scalelayer import  ScaleLayer

seed(1)
tf.random.set_random_seed(2)
config = tf.ConfigProto()  
config.gpu_options.allow_growth=True 
sess = tf.Session(config=config)

K.set_session(sess)

def my_loss_fun(y_true, y_pred):
    # do whatever you want
    return y_pred


def similar_set(X, num_attribs, protected_attribs, constraint):
    # find all similar inputs corresponding to different combinations of protected attributes with non-protected attributes unchanged
    similar_X = []
    protected_domain = []
    for i in protected_attribs:
        protected_domain = protected_domain + [list(range(constraint[i][0], constraint[i][1]+1))]
    all_combs = np.array(list(itertools.product(*protected_domain)))
    for i, comb in enumerate(all_combs):
        X_new = copy.deepcopy(X)
        for a, c in zip(protected_attribs, comb):
            X_new[:, a] = c
        similar_X.append(X_new)
    return similar_X

pos_map = { 'a': [0],
            'r': [6],
            'g': [7],
            'a&r': [0, 6],
            'a&g': [0, 7],
            'r&g': [6, 7]
            }

models_map = {
    'a': "models/gated_models/adult_a_gated_4_0.3_0.2_p-0.3_p0.15.h5",
    'r': "models/gated_models/adult_r_gated_4_0.3_0.2_p-0.95_p0.8.h5",
    'g': "models/gated_models/adult_g_gated_4_0.3_0.2_p-0.6_p0.1.h5",
    'a&r': "models/gated_models/adult_a&r_gated_4_0.3_0.2_p-0.35_p0.25.h5",
    'a&g': "models/gated_models/adult_a&g_gated_4_0.3_0.2_p-0.3_p0.25.h5",
    'r&g': "models/gated_models/adult_r&g_gated_4_0.3_0.2_p-0.9_p0.8.h5",
}

# similar_X = [dis_data, new_data]

layer_map = [('layer1', 'scale_layer_5'), ('layer2', 'scale_layer_6'), ('layer3', 'scale_layer_7'), ('layer4', 'scale_layer_8'), ('layer5', 'layer5'), ('layer5', 'layer6')]

from preprocessing import pre_census_income
from tensorflow.keras.models import Model

for layer_index in range(5, 6):
    print("*"*10, "layer", layer_index+1)
    for attr in pos_map.keys():
        protected_attribs = pos_map[attr]
        
        model_path = models_map[attr]
        # adult_g_gated_4_0.3_0.2_p-0.1_p0.9.h5
        model = keras.models.load_model(model_path, custom_objects={'ScaleLayer': ScaleLayer})
        print(model.get_layer('layer6').get_weights())
#         model.summary()

        # data_name = f"data/adult/C-{attr}_ids_EIDIG_INF.npy"
        # dis_data = np.load(data_name)

        dis_data = pre_census_income.X_train
        num_attribs = len(dis_data[0])
        new_data = dis_data.copy()

        similar_X = similar_set(dis_data, num_attribs, protected_attribs, pre_census_income.constraint)

        # layer_name = layer_map[layer_index][1]
        # inter_model = Model(model.input, model.get_layer(layer_name).output)

        layer_name = layer_map[layer_index][1]
        inter_model = Model(model.input, model.get_layer(layer_name).output)                                 

        inter_output_ori = inter_model.predict(pre_census_income.X_train)
        
        max_v = inter_output_ori.max()
        min_v = inter_output_ori.min()

        diff = 0
        for i in range(len(similar_X)):
            inter_output_adv = inter_model.predict(similar_X[i])
            diff += np.abs(inter_output_adv - inter_output_ori).sum() / (max_v - min_v)

        num = len(similar_X) * similar_X[0].shape[0]
        print("attr:", attr, round(diff/num, 3))

********** layer 6
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
If using Keras pass *_constraint arguments to layers.
[array([[ 2.9423175 ],
       [-1.499268  ],
       [-0.73832774],
       [-0.76415855],
       [ 0.704021  ],
       [-4.6148725 ],
       [-0.95385844],
       [-0.68753624],
       [-1.078599  ],
       [ 1.7334886 ]], dtype=float32), array([-0.18941183], dtype=float32)]
index: 0 [0.17130086]
index: 1 [0.00017318]
index: 2 [0.08544636]
index: 3 [0.1719676]
index: 4 [0.09347486]
index: 5 [0.43749982]
index: 6 [0.06411612]
index: 7 [0.0733448]
index: 8 [0.47903845]
index: 9 [0.00839221]
index: 10 [0.5057362]
index: 11 [0.65876573]
index: 12 [0.6385702]
index: 13 [0.6036915]
index: 14 [0.71504134]
index: 15 [0.01873919]
index: 16 [0.4721572]
index: 17 [0.5

index: 581 [0.4966442]
index: 582 [0.22214234]
index: 583 [0.08745113]
index: 584 [0.59230316]
index: 585 [0.09027717]
index: 586 [0.24980268]
index: 587 [0.12258515]
index: 588 [0.35266882]
index: 589 [0.454067]
index: 590 [0.45760542]
index: 591 [0.1710585]
index: 592 [0.2184104]
index: 593 [0.01418722]
index: 594 [0.15611088]
index: 595 [0.42954847]
index: 596 [0.06544009]
index: 597 [0.6377214]
index: 598 [0.41767752]
index: 599 [0.53060913]
index: 600 [0.16405037]
index: 601 [0.00498471]
index: 602 [0.5870798]
index: 603 [0.06640846]
index: 604 [0.5297827]
index: 605 [0.7152078]
index: 606 [0.11216402]
index: 607 [0.695979]
index: 608 [0.76965207]
index: 609 [0.01792273]
index: 610 [0.07286429]
index: 611 [0.47037995]
index: 612 [0.45824602]
index: 613 [0.04575416]
index: 614 [0.6207359]
index: 615 [0.5976567]
index: 616 [0.05013016]
index: 617 [0.04742065]
index: 618 [0.15984839]
index: 619 [0.11797798]
index: 620 [0.45760542]
index: 621 [0.40507078]
index: 622 [0.14298558]
index

index: 1180 [0.6405973]
index: 1181 [0.5549453]
index: 1182 [0.1542106]
index: 1183 [0.09600884]
index: 1184 [0.16308478]
index: 1185 [0.19544476]
index: 1186 [0.21088201]
index: 1187 [0.3417501]
index: 1188 [0.03638515]
index: 1189 [0.5972597]
index: 1190 [0.34113532]
index: 1191 [0.13627028]
index: 1192 [0.00786933]
index: 1193 [0.19189581]
index: 1194 [0.08071366]
index: 1195 [0.76547545]
index: 1196 [0.16979957]
index: 1197 [0.03596422]
index: 1198 [0.25177848]
index: 1199 [0.07070038]
index: 1200 [0.44497317]
index: 1201 [0.7037542]
index: 1202 [0.36113912]
index: 1203 [0.09027717]
index: 1204 [0.16513842]
index: 1205 [0.6682435]
index: 1206 [0.34519875]
index: 1207 [0.09225792]
index: 1208 [0.06855047]
index: 1209 [0.02973562]
index: 1210 [0.13596418]
index: 1211 [0.09073064]
index: 1212 [0.22687835]
index: 1213 [0.15190402]
index: 1214 [0.45235667]
index: 1215 [0.10437876]
index: 1216 [0.0424566]
index: 1217 [0.36771125]
index: 1218 [0.09600884]
index: 1219 [0.08492169]
index: 1

index: 1760 [0.06170204]
index: 1761 [0.04426202]
index: 1762 [0.11013824]
index: 1763 [0.10009813]
index: 1764 [0.03505167]
index: 1765 [0.08994016]
index: 1766 [0.07514995]
index: 1767 [0.24364653]
index: 1768 [0.10479271]
index: 1769 [0.03429377]
index: 1770 [0.36200732]
index: 1771 [0.02239132]
index: 1772 [0.42165458]
index: 1773 [0.62578005]
index: 1774 [0.35581636]
index: 1775 [0.07292268]
index: 1776 [0.0945524]
index: 1777 [0.56052315]
index: 1778 [0.26988977]
index: 1779 [0.63228387]
index: 1780 [0.51651603]
index: 1781 [0.19687086]
index: 1782 [0.08168468]
index: 1783 [0.1739304]
index: 1784 [0.10009813]
index: 1785 [0.12432402]
index: 1786 [0.39435458]
index: 1787 [0.04251891]
index: 1788 [0.08525234]
index: 1789 [0.6835727]
index: 1790 [0.34647858]
index: 1791 [0.04995644]
index: 1792 [0.3767048]
index: 1793 [0.13596418]
index: 1794 [0.41528523]
index: 1795 [0.03677791]
index: 1796 [0.01368028]
index: 1797 [0.00726384]
index: 1798 [0.5192532]
index: 1799 [0.28765363]
index

index: 2342 [0.66464937]
index: 2343 [0.08397007]
index: 2344 [0.6551219]
index: 2345 [0.6844282]
index: 2346 [0.2586011]
index: 2347 [0.61904705]
index: 2348 [0.09144112]
index: 2349 [0.6973956]
index: 2350 [0.11873254]
index: 2351 [0.76965207]
index: 2352 [0.5693359]
index: 2353 [0.43168113]
index: 2354 [0.57923037]
index: 2355 [0.11672539]
index: 2356 [0.4594249]
index: 2357 [0.4269023]
index: 2358 [0.18703955]
index: 2359 [0.4721572]
index: 2360 [0.29398155]
index: 2361 [0.6096948]
index: 2362 [0.5192532]
index: 2363 [0.48152]
index: 2364 [0.04473159]
index: 2365 [0.44054696]
index: 2366 [0.06217942]
index: 2367 [0.11061141]
index: 2368 [0.03084505]
index: 2369 [0.04797247]
index: 2370 [0.10882026]
index: 2371 [0.20264441]
index: 2372 [0.08538917]
index: 2373 [0.02244577]
index: 2374 [0.2372751]
index: 2375 [0.27411994]
index: 2376 [0.00223383]
index: 2377 [0.45235667]
index: 2378 [0.623515]
index: 2379 [0.44143137]
index: 2380 [0.05167073]
index: 2381 [0.03666916]
index: 2382 [0.4

...

index: 29153 [0.18728188]
index: 29154 [0.02331313]
index: 29155 [0.02061725]
index: 29156 [0.02235758]
index: 29157 [0.03864118]
index: 29158 [0.00122899]
index: 29159 [0.03687394]
index: 29160 [0.18515936]
index: 29161 [0.4019726]
index: 29162 [0.2860649]
index: 29163 [0.3413235]
index: 29164 [0.00261447]
index: 29165 [0.41212183]
index: 29166 [0.75191224]
index: 29167 [0.5374111]
index: 29168 [0.8018093]
index: 29169 [0.22636652]
index: 29170 [0.46850058]
index: 29171 [0.3457895]
index: 29172 [0.34011227]
index: 29173 [0.35354766]
index: 29174 [0.5246257]
index: 29175 [0.14822772]
index: 29176 [0.01684102]
index: 29177 [0.05144259]
index: 29178 [0.8061516]
index: 29179 [0.3672176]
index: 29180 [0.1477887]
index: 29181 [0.28926128]
index: 29182 [0.30447537]
index: 29183 [0.48800766]
index: 29184 [0.06199569]
index: 29185 [0.45002925]
index: 29186 [0.2777648]
index: 29187 [0.03818327]
index: 29188 [0.00596496]
index: 29189 [0.25953266]
index: 29190 [0.2766742]
index: 29191 [0.04620901

index: 29720 [0.01565647]
index: 29721 [0.37985983]
index: 29722 [0.00603837]
index: 29723 [0.02666476]
index: 29724 [0.04965436]
index: 29725 [0.18553033]
index: 29726 [0.116395]
index: 29727 [0.52138156]
index: 29728 [0.02211729]
index: 29729 [0.04605359]
index: 29730 [0.47674772]
index: 29731 [0.4273897]
index: 29732 [0.08757037]
index: 29733 [0.6758204]
index: 29734 [0.1422472]
index: 29735 [0.32788414]
index: 29736 [0.00046745]
index: 29737 [0.35049653]
index: 29738 [0.51201266]
index: 29739 [0.34740674]
index: 29740 [0.40328175]
index: 29741 [0.2107296]
index: 29742 [0.30591583]
index: 29743 [0.01025233]
index: 29744 [0.04841906]
index: 29745 [0.38800818]
index: 29746 [0.55768394]
index: 29747 [0.74281627]
index: 29748 [0.01489154]
index: 29749 [0.7273079]
index: 29750 [0.66602397]
index: 29751 [0.21713981]
index: 29752 [0.15348396]
index: 29753 [0.00814015]
index: 29754 [0.26768214]
index: 29755 [0.13160741]
index: 29756 [0.41170287]
index: 29757 [0.8707244]
index: 29758 [0.2437

index: 30290 [0.03304863]
index: 30291 [0.04661512]
index: 30292 [0.602057]
index: 30293 [0.00741091]
index: 30294 [0.41596165]
index: 30295 [0.07853726]
index: 30296 [0.4340122]
index: 30297 [0.08873659]
index: 30298 [0.0445492]
index: 30299 [0.64629877]
index: 30300 [0.05017304]
index: 30301 [0.7057595]
index: 30302 [0.04125178]
index: 30303 [0.16787037]
index: 30304 [0.18817374]
index: 30305 [0.4244914]
index: 30306 [0.04478145]
index: 30307 [0.03085953]
index: 30308 [0.59004724]
index: 30309 [0.11583632]
index: 30310 [0.19677171]
index: 30311 [0.46221596]
index: 30312 [0.75260365]
index: 30313 [0.09416538]
index: 30314 [0.00330582]
index: 30315 [0.00667551]
index: 30316 [0.60116833]
index: 30317 [0.2595197]
index: 30318 [0.07344797]
index: 30319 [0.70012414]
index: 30320 [0.04872328]
index: 30321 [0.2465817]
index: 30322 [0.093445]
index: 30323 [0.05152068]
index: 30324 [0.48941606]
index: 30325 [0.42225176]
index: 30326 [0.05422571]
index: 30327 [0.4014586]
index: 30328 [0.6762743

index: 30856 [0.68589723]
index: 30857 [0.21125633]
index: 30858 [0.04177645]
index: 30859 [0.04387632]
index: 30860 [0.74281627]
index: 30861 [0.7207315]
index: 30862 [0.600255]
index: 30863 [0.25864628]
index: 30864 [0.8182503]
index: 30865 [0.00677633]
index: 30866 [0.02097985]
index: 30867 [0.02810603]
index: 30868 [0.54695785]
index: 30869 [0.13728744]
index: 30870 [0.4474703]
index: 30871 [0.03159612]
index: 30872 [0.31652364]
index: 30873 [0.02241251]
index: 30874 [0.0481008]
index: 30875 [0.8117982]
index: 30876 [0.08684188]
index: 30877 [0.0226391]
index: 30878 [0.4325721]
index: 30879 [0.08351216]
index: 30880 [0.27557763]
index: 30881 [0.32625216]
index: 30882 [0.06099376]
index: 30883 [0.09775737]
index: 30884 [0.90074825]
index: 30885 [0.84883237]
index: 30886 [0.02648482]
index: 30887 [0.0213151]
index: 30888 [0.22627273]
index: 30889 [0.65445644]
index: 30890 [0.01524398]
index: 30891 [0.00099763]
index: 30892 [0.71298945]
index: 30893 [0.08428079]
index: 30894 [0.300654

KeyboardInterrupt: 

In [3]:
from tensorflow import keras
import os
import joblib
import numpy as np
from explain import  get_relevance, get_critical_neurons
import tensorflow as tf
# from tensorflow import set_random_seed
from scalelayer import  ScaleLayer
from numpy.random import seed
import itertools
import time
import copy
from preprocessing import pre_bank_marketing
import tensorflow.keras.backend as K
import argparse

seed(1)
tf.random.set_random_seed(2)
config = tf.ConfigProto()  
config.gpu_options.allow_growth=True 
sess = tf.Session(config=config)

K.set_session(sess)

def my_loss_fun(y_true, y_pred):
    # do whatever you want
    return y_pred

    
model = keras.Sequential([
    keras.layers.Dense(30, activation="relu", input_shape=pre_bank_marketing.X_train.shape[1:]),
    keras.layers.Dense(20, activation="relu"),
    keras.layers.Dense(15, activation="relu"),
    keras.layers.Dense(15, activation="relu"),
    keras.layers.Dense(10, activation="relu"),
    keras.layers.Dense(1, activation="sigmoid")
])

def similar_set(X, num_attribs, protected_attribs, constraint):
    # find all similar inputs corresponding to different combinations of protected attributes with non-protected attributes unchanged
    similar_X = []
    protected_domain = []
    for i in protected_attribs:
        protected_domain = protected_domain + [list(range(constraint[i][0], constraint[i][1]+1))]
    all_combs = np.array(list(itertools.product(*protected_domain)))
    for i, comb in enumerate(all_combs):
        X_new = copy.deepcopy(X)
        for a, c in zip(protected_attribs, comb):
            X_new[:, a] = c
        similar_X.append(X_new)
    return similar_X

pos_map = { 'a': [0],
            }

model_path = "models/gated_models/bank_a_gated_4_0.3_0.2_p-0.15_p0.3.h5"
# adult_g_gated_4_0.3_0.2_p-0.1_p0.9.h5
model = keras.models.load_model(model_path, custom_objects={'ScaleLayer': ScaleLayer})
model.summary()

# similar_X = [dis_data, new_data]

layer_map = [('dense_132', 'scale_layer_5'), ('dense_133', 'scale_layer_6'), ('dense_134', 'scale_layer_7'), ('dense_135', 'scale_layer_8'), ('dense_136', 'layer5')]

from preprocessing import pre_bank_marketing
from tensorflow.keras.models import Model

for layer_index in range(5):
    print("layer", layer_index)
    for attr in pos_map.keys():
        protected_attribs = pos_map[attr]

        # data_name = f"data/adult/C-{attr}_ids_EIDIG_INF.npy"
        # dis_data = np.load(data_name)

        dis_data = pre_bank_marketing.X_train
        num_attribs = len(dis_data[0])
        new_data = dis_data.copy()

        similar_X = similar_set(dis_data, num_attribs, protected_attribs, pre_bank_marketing.constraint)

        # layer_name = layer_map[layer_index][1]
        # inter_model = Model(model.input, model.get_layer(layer_name).output)

        layer_name = layer_map[layer_index][1]
        inter_model = Model(model.input, model.get_layer(layer_name).output)                                 

        inter_output_ori = inter_model.predict(pre_bank_marketing.X_train)
        
        max_v = inter_output_ori.max()
        min_v = inter_output_ori.min()

        diff = 0
        for i in range(len(similar_X)):
            inter_output_adv = inter_model.predict(similar_X[i])
            diff += np.abs(inter_output_adv - inter_output_ori).sum() / (max_v - min_v)

        num = len(similar_X) * similar_X[0].shape[0]
        print("attr:", attr, round(diff/num, 3))

Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         [(None, 16)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 30)                510       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer2 (Dense)               (None, 20)                620       
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 20)                20        
_________________________________________________________________
layer3 (Dense)               (None, 15)                315       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)                15  

In [8]:
from tensorflow import keras
import os
import joblib
import numpy as np
from explain import  get_relevance, get_critical_neurons
import tensorflow as tf
# from tensorflow import set_random_seed
from scalelayer import  ScaleLayer
from numpy.random import seed
import itertools
import time
import copy
from preprocessing import pre_census_income
import tensorflow.keras.backend as K
import argparse
from scalelayer import  ScaleLayer

seed(1)
tf.random.set_random_seed(2)
config = tf.ConfigProto()  
config.gpu_options.allow_growth=True 
sess = tf.Session(config=config)

K.set_session(sess)

def my_loss_fun(y_true, y_pred):
    # do whatever you want
    return y_pred


def similar_set(X, num_attribs, protected_attribs, constraint):
    # find all similar inputs corresponding to different combinations of protected attributes with non-protected attributes unchanged
    similar_X = []
    protected_domain = []
    for i in protected_attribs:
        protected_domain = protected_domain + [list(range(constraint[i][0], constraint[i][1]+1))]
    all_combs = np.array(list(itertools.product(*protected_domain)))
    for i, comb in enumerate(all_combs):
        X_new = copy.deepcopy(X)
        for a, c in zip(protected_attribs, comb):
            X_new[:, a] = c
        similar_X.append(X_new)
    return similar_X

pos_map = { 'a': [0],
            'r': [6],
            'g': [7],
            'a&r': [0, 6],
            'a&g': [0, 7],
            'r&g': [6, 7]
            }

model_map = {
    'a': "models/diff_adult_a_gated_4_diff.h5",
    'r': "models/diff_adult_r_gated_4_diff.h5",
    'g': "models/diff_adult_g_gated_4_diff.h5",
    'a&r': "models/diff_adult_a&r_gated_4_diff.h5",
    'a&g': "models/diff_adult_a&g_gated_4_diff.h5",
    'r&g': "models/diff_adult_r&g_gated_4_diff.h5",
}

# similar_X = [dis_data, new_data]

layer_map = [('layer1', 'scale_layer_5'), ('layer2', 'scale_layer_6'), ('layer3', 'scale_layer_7'), ('layer4', 'scale_layer_8'), ('layer5', 'layer5')]

from preprocessing import pre_census_income
from tensorflow.keras.models import Model

for layer_index in range(5):
    print("layer", layer_index)
    for attr in pos_map.keys():
        protected_attribs = pos_map[attr]
        
        model_path = model_map[attr]
        # adult_g_gated_4_0.3_0.2_p-0.1_p0.9.h5
        model = keras.models.load_model(model_path, custom_objects={'ScaleLayer': ScaleLayer})
        model.summary()

        # data_name = f"data/adult/C-{attr}_ids_EIDIG_INF.npy"
        # dis_data = np.load(data_name)

        dis_data = pre_census_income.X_train
        num_attribs = len(dis_data[0])
        new_data = dis_data.copy()

        similar_X = similar_set(dis_data, num_attribs, protected_attribs, pre_census_income.constraint)

        # layer_name = layer_map[layer_index][1]
        # inter_model = Model(model.input, model.get_layer(layer_name).output)

        layer_name = layer_map[layer_index][1]
        inter_model = Model(model.input, model.get_layer(layer_name).output)                                 

        inter_output_ori = inter_model.predict(pre_census_income.X_train)
        
        max_v = inter_output_ori.max()
        min_v = inter_output_ori.min()

        diff = 0
        for i in range(len(similar_X)):
            inter_output_adv = inter_model.predict(similar_X[i])
            diff += np.abs(inter_output_adv - inter_output_ori).sum() / (max_v - min_v)

        num = len(similar_X) * similar_X[0].shape[0]
        print("attr:", attr, round(diff/num, 3))
                                 

layer 0
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 12)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 30)                390       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer2 (Dense)               (None, 20)                620       
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 20)                20        
_________________________________________________________________
layer3 (Dense)               (None, 15)                315       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)            

attr: a&g 0.096
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 12)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 30)                390       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer2 (Dense)               (None, 20)                620       
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 20)                20        
_________________________________________________________________
layer3 (Dense)               (None, 15)                315       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)    

attr: a&r 0.028
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 12)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 30)                390       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer2 (Dense)               (None, 20)                620       
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 20)                20        
_________________________________________________________________
layer3 (Dense)               (None, 15)                315       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)    

attr: g 0.001
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 12)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 30)                390       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer2 (Dense)               (None, 20)                620       
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 20)                20        
_________________________________________________________________
layer3 (Dense)               (None, 15)                315       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)      

attr: r 0.001
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 12)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 30)                390       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer2 (Dense)               (None, 20)                620       
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 20)                20        
_________________________________________________________________
layer3 (Dense)               (None, 15)                315       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)      

attr: a 0.003
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 12)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 30)                390       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer2 (Dense)               (None, 20)                620       
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 20)                20        
_________________________________________________________________
layer3 (Dense)               (None, 15)                315       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)      

attr: r&g 0.053


In [8]:
from tensorflow import keras
import os
import joblib
import numpy as np
from explain import  get_relevance, get_critical_neurons
import tensorflow as tf
# from tensorflow import set_random_seed
from scalelayer import  ScaleLayer
from numpy.random import seed
import itertools
import time
import copy
from preprocessing import pre_bank_marketing
import tensorflow.keras.backend as K
import argparse

seed(1)
tf.random.set_random_seed(2)
config = tf.ConfigProto()  
config.gpu_options.allow_growth=True 
sess = tf.Session(config=config)

K.set_session(sess)

def my_loss_fun(y_true, y_pred):
    # do whatever you want
    return y_pred

    
model = keras.Sequential([
    keras.layers.Dense(30, activation="relu", input_shape=pre_bank_marketing.X_train.shape[1:]),
    keras.layers.Dense(20, activation="relu"),
    keras.layers.Dense(15, activation="relu"),
    keras.layers.Dense(15, activation="relu"),
    keras.layers.Dense(10, activation="relu"),
    keras.layers.Dense(1, activation="sigmoid")
])

def similar_set(X, num_attribs, protected_attribs, constraint):
    # find all similar inputs corresponding to different combinations of protected attributes with non-protected attributes unchanged
    similar_X = []
    protected_domain = []
    for i in protected_attribs:
        protected_domain = protected_domain + [list(range(constraint[i][0], constraint[i][1]+1))]
    all_combs = np.array(list(itertools.product(*protected_domain)))
    for i, comb in enumerate(all_combs):
        X_new = copy.deepcopy(X)
        for a, c in zip(protected_attribs, comb):
            X_new[:, a] = c
        similar_X.append(X_new)
    return similar_X

pos_map = { 'a': [0],
            }

model_path = "models/gated_models_diff/diff_bank_a_gated_4_diff.h5"
# adult_g_gated_4_0.3_0.2_p-0.1_p0.9.h5
model = keras.models.load_model(model_path, custom_objects={'ScaleLayer': ScaleLayer})
model.summary()

# similar_X = [dis_data, new_data]

layer_map = [('dense_132', 'scale_layer_5'), ('dense_133', 'scale_layer_6'), ('dense_134', 'scale_layer_7'), ('dense_135', 'scale_layer_8'), ('dense_136', 'layer5')]

from preprocessing import pre_bank_marketing
from tensorflow.keras.models import Model

for layer_index in range(5):
    print("layer", layer_index)
    for attr in pos_map.keys():
        protected_attribs = pos_map[attr]

        # data_name = f"data/adult/C-{attr}_ids_EIDIG_INF.npy"
        # dis_data = np.load(data_name)

        dis_data = pre_bank_marketing.X_train
        num_attribs = len(dis_data[0])
        new_data = dis_data.copy()

        similar_X = similar_set(dis_data, num_attribs, protected_attribs, pre_bank_marketing.constraint)

        # layer_name = layer_map[layer_index][1]
        # inter_model = Model(model.input, model.get_layer(layer_name).output)

        layer_name = layer_map[layer_index][1]
        inter_model = Model(model.input, model.get_layer(layer_name).output)                                 

        inter_output_ori = inter_model.predict(pre_bank_marketing.X_train)
        
        max_v = inter_output_ori.max()
        min_v = inter_output_ori.min()

        diff = 0
        for i in range(len(similar_X)):
            inter_output_adv = inter_model.predict(similar_X[i])
            diff += np.abs(inter_output_adv - inter_output_ori).sum() / (max_v - min_v)

        num = len(similar_X) * similar_X[0].shape[0]
        print("attr:", attr, round(diff/num, 3))

Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 16)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 30)                510       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer2 (Dense)               (None, 20)                620       
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 20)                20        
_________________________________________________________________
layer3 (Dense)               (None, 15)                315       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)                15  

In [4]:
from tensorflow import keras
import os
import joblib
import numpy as np
from explain import  get_relevance, get_critical_neurons
import tensorflow as tf
# from tensorflow import set_random_seed
from scalelayer import  ScaleLayer
from numpy.random import seed
import itertools
import time
import copy
from preprocessing import pre_lsac
import tensorflow.keras.backend as K
import argparse

seed(1)
tf.random.set_random_seed(2)
config = tf.ConfigProto()  
config.gpu_options.allow_growth=True 
sess = tf.Session(config=config)

K.set_session(sess)

def my_loss_fun(y_true, y_pred):
    # do whatever you want
    return y_pred

    
model = keras.Sequential([
    keras.layers.Dense(50, activation="relu", input_shape=pre_lsac.X_train.shape[1:]),
    keras.layers.Dense(30, activation="relu"),
    keras.layers.Dense(15, activation="relu"),
    keras.layers.Dense(10, activation="relu"),
    keras.layers.Dense(5, activation="relu"),
    keras.layers.Dense(1, activation="sigmoid")
])

def similar_set(X, num_attribs, protected_attribs, constraint):
    # find all similar inputs corresponding to different combinations of protected attributes with non-protected attributes unchanged
    similar_X = []
    protected_domain = []
    for i in protected_attribs:
        protected_domain = protected_domain + [list(range(int(constraint[i][0]), int(constraint[i][1]+1)))]
    all_combs = np.array(list(itertools.product(*protected_domain)))
    for i, comb in enumerate(all_combs):
        X_new = copy.deepcopy(X)
        for a, c in zip(protected_attribs, comb):
            X_new[:, a] = c
        similar_X.append(X_new)
    return similar_X

pos_map = { 
            'r': [10],
            'g': [9],
            'g&r': [10, 9],
            }

models_map = {
            'r': 'models/gated_models/lsac_r_gated_4_0.3_0.2_p-0.9_p0.05.h5',
            'g': 'models/gated_models/lsac_g_gated_4_0.3_0.2_p-0.85_p0.2.h5',
            'g&r': 'models/gated_models/lsac_g&r_gated_4_0.3_0.2_p-0.55_p0.45.h5',
}



# similar_X = [dis_data, new_data]

layer_map = [('layer5', 'scale_layer_5'), ('layer5', 'scale_layer_6'), ('layer5', 'scale_layer_7'), ('layer5', 'scale_layer_8'), ('layer5', 'layer5')]

from preprocessing import pre_lsac
from tensorflow.keras.models import Model

for layer_index in range(0, 5):
    print("layer", layer_index)
    for attr in pos_map.keys():
        protected_attribs = pos_map[attr]

        # data_name = f"data/adult/C-{attr}_ids_EIDIG_INF.npy"
        # dis_data = np.load(data_name)
        model_path = models_map[attr]
        # adult_g_gated_4_0.3_0.2_p-0.1_p0.9.h5
        model = keras.models.load_model(model_path, custom_objects={'ScaleLayer': ScaleLayer})
        model.summary()

        dis_data = pre_lsac.X_train
        num_attribs = len(dis_data[0])
        new_data = dis_data.copy()

        similar_X = similar_set(dis_data, num_attribs, protected_attribs, pre_lsac.constraint)

        # layer_name = layer_map[layer_index][1]
        # inter_model = Model(model.input, model.get_layer(layer_name).output)

        layer_name = layer_map[layer_index][1]
        inter_model = Model(model.input, model.get_layer(layer_name).output)                                 

        inter_output_ori = inter_model.predict(pre_lsac.X_train)
        
        max_v = inter_output_ori.max()
        min_v = inter_output_ori.min()

        diff = 0
        for i in range(len(similar_X)):
            inter_output_adv = inter_model.predict(similar_X[i])
            diff += np.abs(inter_output_adv - inter_output_ori).sum() / (max_v - min_v)

        num = len(similar_X) * similar_X[0].shape[0]
        print("attr:", attr, round(diff/num, 3))

layer 0
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         [(None, 11)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 50)                600       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 50)                50        
_________________________________________________________________
layer2 (Dense)               (None, 30)                1530      
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer3 (Dense)               (None, 15)                465       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)            

attr: g 0.089
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         [(None, 11)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 50)                600       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 50)                50        
_________________________________________________________________
layer2 (Dense)               (None, 30)                1530      
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer3 (Dense)               (None, 15)                465       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)      

attr: r 0.072
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         [(None, 11)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 50)                600       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 50)                50        
_________________________________________________________________
layer2 (Dense)               (None, 30)                1530      
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer3 (Dense)               (None, 15)                465       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)      

attr: g&r 0.073


In [9]:
from tensorflow import keras
import os
import joblib
import numpy as np
from explain import  get_relevance, get_critical_neurons
import tensorflow as tf
# from tensorflow import set_random_seed
from scalelayer import  ScaleLayer
from numpy.random import seed
import itertools
import time
import copy
from preprocessing import pre_lsac
import tensorflow.keras.backend as K
import argparse
from scalelayer import  ScaleLayer

seed(1)
tf.random.set_random_seed(2)
config = tf.ConfigProto()  
config.gpu_options.allow_growth=True 
sess = tf.Session(config=config)

K.set_session(sess)

def my_loss_fun(y_true, y_pred):
    # do whatever you want
    return y_pred

    
model = keras.Sequential([
    keras.layers.Dense(50, activation="relu", input_shape=pre_lsac.X_train.shape[1:]),
    keras.layers.Dense(30, activation="relu"),
    keras.layers.Dense(15, activation="relu"),
    keras.layers.Dense(10, activation="relu"),
    keras.layers.Dense(5, activation="relu"),
    keras.layers.Dense(1, activation="sigmoid")
])

def similar_set(X, num_attribs, protected_attribs, constraint):
    # find all similar inputs corresponding to different combinations of protected attributes with non-protected attributes unchanged
    similar_X = []
    protected_domain = []
    for i in protected_attribs:
        protected_domain = protected_domain + [list(range(int(constraint[i][0]), int(constraint[i][1]+1)))]
    all_combs = np.array(list(itertools.product(*protected_domain)))
    for i, comb in enumerate(all_combs):
        X_new = copy.deepcopy(X)
        for a, c in zip(protected_attribs, comb):
            X_new[:, a] = c
        similar_X.append(X_new)
    return similar_X

pos_map = { 
            'r': [10],
            'g': [9],
            'g&r': [10, 9],
            }

models_map = {
            'r': 'models/gated_models_diff/diff_lsac_r_gated_4_diff.h5',
            'g': 'models/gated_models_diff/diff_lsac_g_gated_4_diff.h5',
            'g&r': 'models/gated_models_diff/diff_lsac_g&r_gated_4_diff.h5',
}



# similar_X = [dis_data, new_data]

layer_map = [('layer5', 'scale_layer_5'), ('layer5', 'scale_layer_6'), ('layer5', 'scale_layer_7'), ('layer5', 'scale_layer_8'), ('layer5', 'layer5')]

from preprocessing import pre_lsac
from tensorflow.keras.models import Model

for layer_index in range(0, 5):
    print("layer", layer_index)
    for attr in pos_map.keys():
        protected_attribs = pos_map[attr]

        # data_name = f"data/adult/C-{attr}_ids_EIDIG_INF.npy"
        # dis_data = np.load(data_name)
        model_path = models_map[attr]
        # adult_g_gated_4_0.3_0.2_p-0.1_p0.9.h5
        model = tf.keras.models.load_model(model_path, custom_objects={'ScaleLayer': ScaleLayer})
        model.summary()

        dis_data = pre_lsac.X_train
        num_attribs = len(dis_data[0])
        new_data = dis_data.copy()

        similar_X = similar_set(dis_data, num_attribs, protected_attribs, pre_lsac.constraint)

        # layer_name = layer_map[layer_index][1]
        # inter_model = Model(model.input, model.get_layer(layer_name).output)

        layer_name = layer_map[layer_index][1]
        inter_model = Model(model.input, model.get_layer(layer_name).output)                                 

        inter_output_ori = inter_model.predict(pre_lsac.X_train)

        max_v = inter_output_ori.max()
        min_v = inter_output_ori.min()
        
        diff = 0
        for i in range(len(similar_X)):
            inter_output_adv = inter_model.predict(similar_X[i])
            diff += np.abs(inter_output_adv - inter_output_ori).sum()

        num = len(similar_X) * similar_X[0].shape[0]
        print("attr:", attr, round(diff/num, 3))

layer 0
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 11)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 50)                600       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 50)                50        
_________________________________________________________________
layer2 (Dense)               (None, 30)                1530      
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer3 (Dense)               (None, 15)                465       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)            

attr: g 0.121
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 11)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 50)                600       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 50)                50        
_________________________________________________________________
layer2 (Dense)               (None, 30)                1530      
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer3 (Dense)               (None, 15)                465       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)      

attr: r 0.063
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 11)]              0         
_________________________________________________________________
layer1 (Dense)               (None, 50)                600       
_________________________________________________________________
scale_layer_5 (ScaleLayer)   (None, 50)                50        
_________________________________________________________________
layer2 (Dense)               (None, 30)                1530      
_________________________________________________________________
scale_layer_6 (ScaleLayer)   (None, 30)                30        
_________________________________________________________________
layer3 (Dense)               (None, 15)                465       
_________________________________________________________________
scale_layer_7 (ScaleLayer)   (None, 15)      

attr: g&r 0.024
